#1. Data Loading

importing required libraries

In [0]:
from pyspark.sql.functions import *
from pyspark.sql.types import *
from pyspark.sql.window import Window
from pyspark.sql import functions as F

In [0]:
df=spark.read.format("json")\
  .option("multine","true")\
    .option("inferschema","true")\
      .load("/FileStore/tables/file1.json")

country_code_df=spark.read.format("csv")\
  .option("header","true")\
    .option("inferschema","true")\
        .load("/FileStore/tables/Country_Code.csv")

#2. Data Exploration and Cleaning

In [0]:
df.show()

+----+-------+--------------------+-------------+-------------+-------------+------+
|code|message|         restaurants|results_found|results_shown|results_start|status|
+----+-------+--------------------+-------------+-------------+-------------+------+
|null|   null|[{{{308322}, b90e...|        17151|           20|            1|  null|
|null|   null|[{{{18017612}, b9...|         4748|           20|            1|  null|
|null|   null|[{{{18313566}, b9...|        13786|           20|            1|  null|
|null|   null|[{{{18353121}, b9...|        10224|           20|            1|  null|
|null|   null|[{{{18354483}, b9...|         7039|           20|            1|  null|
|null|   null|[{{{18452864}, b9...|         5678|           20|            1|  null|
|null|   null|[{{{72604}, b90e6...|         5374|           20|            1|  null|
|null|   null|[{{{801269}, b90e...|         1382|           20|            1|  null|
|null|   null|[{{{900524}, b90e...|         1534|           20|  

In [0]:
country_code_df.display()

Country Code Country 1 India 14 Australia 30 Brazil 37 Canada 94 Indonesia 148 New Zealand 162 Phillipines 166 Qatar 184 Singapore 189 South Africa 191 Sri Lanka 208 Turkey 214 UAE 215 United Kingdom 216 United States

flatten nested json

In [0]:
df.printSchema()

root
 |-- code: long (nullable = true)
 |-- message: string (nullable = true)
 |-- restaurants: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- restaurant: struct (nullable = true)
 |    |    |    |-- R: struct (nullable = true)
 |    |    |    |    |-- res_id: long (nullable = true)
 |    |    |    |-- apikey: string (nullable = true)
 |    |    |    |-- average_cost_for_two: long (nullable = true)
 |    |    |    |-- book_url: string (nullable = true)
 |    |    |    |-- cuisines: string (nullable = true)
 |    |    |    |-- currency: string (nullable = true)
 |    |    |    |-- deeplink: string (nullable = true)
 |    |    |    |-- establishment_types: array (nullable = true)
 |    |    |    |    |-- element: string (containsNull = true)
 |    |    |    |-- events_url: string (nullable = true)
 |    |    |    |-- featured_image: string (nullable = true)
 |    |    |    |-- has_online_delivery: long (nullable = true)
 |    |    |    |-- has_tabl

In [0]:
df1=df.select("*",explode("restaurants").alias("new_restaurants")).drop("restaurants")
df1.printSchema()

root
 |-- code: long (nullable = true)
 |-- message: string (nullable = true)
 |-- results_found: long (nullable = true)
 |-- results_shown: long (nullable = true)
 |-- results_start: string (nullable = true)
 |-- status: string (nullable = true)
 |-- new_restaurants: struct (nullable = true)
 |    |-- restaurant: struct (nullable = true)
 |    |    |-- R: struct (nullable = true)
 |    |    |    |-- res_id: long (nullable = true)
 |    |    |-- apikey: string (nullable = true)
 |    |    |-- average_cost_for_two: long (nullable = true)
 |    |    |-- book_url: string (nullable = true)
 |    |    |-- cuisines: string (nullable = true)
 |    |    |-- currency: string (nullable = true)
 |    |    |-- deeplink: string (nullable = true)
 |    |    |-- establishment_types: array (nullable = true)
 |    |    |    |-- element: string (containsNull = true)
 |    |    |-- events_url: string (nullable = true)
 |    |    |-- featured_image: string (nullable = true)
 |    |    |-- has_online_deliv

In [0]:
new_df=df1.select("*","new_restaurants.restaurant.R.res_id","new_restaurants.restaurant.name","new_restaurants.restaurant.location.country_id","new_restaurants.restaurant.location.city","new_restaurants.restaurant.location.address","new_restaurants.restaurant.location.locality","new_restaurants.restaurant.location.locality_verbose","new_restaurants.restaurant.location.longitude","new_restaurants.restaurant.location.latitude","new_restaurants.restaurant.cuisines","new_restaurants.restaurant.average_cost_for_two","new_restaurants.restaurant.currency","new_restaurants.restaurant.has_online_delivery","new_restaurants.restaurant.is_delivering_now","new_restaurants.restaurant.has_table_booking","new_restaurants.restaurant.switch_to_order_menu","new_restaurants.restaurant.price_range","new_restaurants.restaurant.user_rating.aggregate_rating","new_restaurants.restaurant.user_rating.rating_color","new_restaurants.restaurant.user_rating.rating_text","new_restaurants.restaurant.user_rating.votes")

In [0]:
new_df=new_df.drop("results_start","code","message","results_found","results_shown","resukts_start","status","new_restaurants")
new_df.display()

res_id name country_id city address locality locality_verbose longitude latitude cuisines average_cost_for_two currency has_online_delivery is_delivering_now has_table_booking switch_to_order_menu price_range aggregate_rating rating_color rating_text votes 308322 Hauz Khas Social 1 New Delhi 9-A & 12, Hauz Khas Village, New Delhi Hauz Khas Village Hauz Khas Village, New Delhi 77.1944706000 28.5542851000 Continental, American, Asian, North Indian 1600 Rs. 1 0 1 0 3 4.3 5BA829 Very Good 7931 18037817 Qubitos - The Terrace Cafe 1 New Delhi C-7, Vishal Enclave, Opposite Metro Pillar 417, Rajouri Garden, New Delhi Rajouri Garden Rajouri Garden, New Delhi 77.1177015000 28.6471325000 Thai, European, Mexican, North Indian, Chinese, Cafe 1500 Rs. 0 0 1 0 3 4.5 3F7E00 Excellent 778 312345 The Hudson Cafe 1 New Delhi 2524, 1st Floor, Hudson Lane, Delhi University-GTB Nagar, New Delhi Delhi University-GTB Nagar Delhi University-GTB Nagar, New Delhi 77.2043172000 28.6949468000 Cafe, Italian, Continental, Chinese 850 Rs. 1 0 0 0 2 4.4 5BA829 Very Good 1537 307490 Summer House Cafe 1 New Delhi 1st Floor, DDA Shopping Complex, Aurobindo Place, Hauz Khas, New Delhi Hauz Khas Hauz Khas, New Delhi 77.2038090000 28.5525204000 Italian, Continental 1850 Rs. 0 0 1 0 3 4.1 5BA829 Very Good 1823 18241537 38 Barracks 1 New Delhi M-38, Outer Circle, Connaught Place, New Delhi Connaught Place Connaught Place, New Delhi 77.2228584811 28.6330248887 North Indian, Italian, Asian, American 1600 Rs. 0 0 1 0 3 4.4 5BA829 Very Good 840 18161577 Spezia Bistro 1 New Delhi 2525, 1st Floor, Hudson Lane, Delhi University-GTB Nagar, New Delhi Delhi University-GTB Nagar Delhi University-GTB Nagar, New Delhi 77.2041413000 28.6948390000 Cafe, Continental, Chinese, Italian 900 Rs. 1 0 1 0 2 4.6 3F7E00 Excellent 1071 303960 Manhattan Brewery & Bar Exchange 1 Gurgaon 1st Floor, Global Foyer Mall, Sector 43, Golf Course Road, Gurgaon Global Foyer Mall, Golf Course Road Global Foyer Mall, Golf Course Road, Gurgaon 77.0950273000 28.4602710000 Finger Food, American, Continental, North Indian, Italian 2000 Rs. 0 0 0 0 4 4.6 3F7E00 Excellent 2093 306134 The Wine Company 1 Gurgaon Cyber Hub, DLF Cyber City, Gurgaon Cyber Hub, DLF Cyber City Cyber Hub, DLF Cyber City, Gurgaon 77.0890476000 28.4962285000 Italian, European 2000 Rs. 0 0 1 0 4 2.4 FF7800 Poor 2412 18233593 Farzi Cafe 1 New Delhi 38/39, Level 1, Block E , Inner Circle, Connaught Place, New Delhi Connaught Place Connaught Place, New Delhi 77.2214296000 28.6323984000 Modern Indian 2200 Rs. 0 0 0 0 4 4.4 5BA829 Very Good 1942 7528 Indian Grill Room 1 Gurgaon 315, 3rd Floor, Suncity Business Tower, Golf Course Road, Gurgaon Suncity Business Tower, Golf Course Road Suncity Business Tower, Golf Course Road, Gurgaon 77.1052774000 28.4334574000 North Indian, Mughlai 1800 Rs. 1 0 1 0 3 4.5 3F7E00 Excellent 1262 18273624 Cafeteria & Co. 1 New Delhi G 14, Hudson Lane, Vijay Nagar, New Delhi Vijay Nagar Vijay Nagar, New Delhi 77.2043384000 28.6944707000 Continental, Mexican 900 Rs. 0 0 0 0 2 4.6 3F7E00 Excellent 1136 308022 Farzi Cafe 1 Gurgaon 7-8, Ground Floor, Cyber Hub, DLF Cyber City, Gurgaon Cyber Hub, DLF Cyber City Cyber Hub, DLF Cyber City, Gurgaon 77.0886879000 28.4952079000 Modern Indian 2200 Rs. 0 0 0 0 4 4.3 5BA829 Very Good 4385 18157413 Molecule Air Bar 1 Gurgaon 4th Floor, SCO 53, Main Market, Sector 29, Gurgaon Sector 29 Sector 29, Gurgaon 77.0642265000 28.4679344000 Continental, North Indian, Italian, Chinese 1500 Rs. 0 0 1 0 3 4.2 5BA829 Very Good 1809 18279449 HotMess 1 New Delhi M-11, Middle Circle, Connaught Place, New Delhi Connaught Place Connaught Place, New Delhi 77.2222380000 28.6326547000 North Indian, Mediterranean, Asian, Fast Food 1900 Rs. 1 0 1 0 3 4.3 5BA829 Very Good 1129 311057 My Bar Headquarters 1 New Delhi N-49, 2nd Floor, Connaught Place, New Delhi Connaught Place Connaught Place, New Delhi 77.2198128000 28.6307210000 North Indian, Mughlai, Chinese 1000 Rs. 0 0 0 0 3 3.7 9ACD32 Good 3010 18235

In [0]:
#new_df.filter(col('res_id').isNull()).count()
#new_df.filter(col("name").isNull()).count()
#new_df.filter(col("city").isNull()).count()
#new_df.filter(col("average_cost_for_two").isNull()).count()

In [0]:
new_df=new_df.dropna()
new_df.display()

res_id name country_id city address locality locality_verbose longitude latitude cuisines average_cost_for_two currency has_online_delivery is_delivering_now has_table_booking switch_to_order_menu price_range aggregate_rating rating_color rating_text votes 308322 Hauz Khas Social 1 New Delhi 9-A & 12, Hauz Khas Village, New Delhi Hauz Khas Village Hauz Khas Village, New Delhi 77.1944706000 28.5542851000 Continental, American, Asian, North Indian 1600 Rs. 1 0 1 0 3 4.3 5BA829 Very Good 7931 18037817 Qubitos - The Terrace Cafe 1 New Delhi C-7, Vishal Enclave, Opposite Metro Pillar 417, Rajouri Garden, New Delhi Rajouri Garden Rajouri Garden, New Delhi 77.1177015000 28.6471325000 Thai, European, Mexican, North Indian, Chinese, Cafe 1500 Rs. 0 0 1 0 3 4.5 3F7E00 Excellent 778 312345 The Hudson Cafe 1 New Delhi 2524, 1st Floor, Hudson Lane, Delhi University-GTB Nagar, New Delhi Delhi University-GTB Nagar Delhi University-GTB Nagar, New Delhi 77.2043172000 28.6949468000 Cafe, Italian, Continental, Chinese 850 Rs. 1 0 0 0 2 4.4 5BA829 Very Good 1537 307490 Summer House Cafe 1 New Delhi 1st Floor, DDA Shopping Complex, Aurobindo Place, Hauz Khas, New Delhi Hauz Khas Hauz Khas, New Delhi 77.2038090000 28.5525204000 Italian, Continental 1850 Rs. 0 0 1 0 3 4.1 5BA829 Very Good 1823 18241537 38 Barracks 1 New Delhi M-38, Outer Circle, Connaught Place, New Delhi Connaught Place Connaught Place, New Delhi 77.2228584811 28.6330248887 North Indian, Italian, Asian, American 1600 Rs. 0 0 1 0 3 4.4 5BA829 Very Good 840 18161577 Spezia Bistro 1 New Delhi 2525, 1st Floor, Hudson Lane, Delhi University-GTB Nagar, New Delhi Delhi University-GTB Nagar Delhi University-GTB Nagar, New Delhi 77.2041413000 28.6948390000 Cafe, Continental, Chinese, Italian 900 Rs. 1 0 1 0 2 4.6 3F7E00 Excellent 1071 303960 Manhattan Brewery & Bar Exchange 1 Gurgaon 1st Floor, Global Foyer Mall, Sector 43, Golf Course Road, Gurgaon Global Foyer Mall, Golf Course Road Global Foyer Mall, Golf Course Road, Gurgaon 77.0950273000 28.4602710000 Finger Food, American, Continental, North Indian, Italian 2000 Rs. 0 0 0 0 4 4.6 3F7E00 Excellent 2093 306134 The Wine Company 1 Gurgaon Cyber Hub, DLF Cyber City, Gurgaon Cyber Hub, DLF Cyber City Cyber Hub, DLF Cyber City, Gurgaon 77.0890476000 28.4962285000 Italian, European 2000 Rs. 0 0 1 0 4 2.4 FF7800 Poor 2412 18233593 Farzi Cafe 1 New Delhi 38/39, Level 1, Block E , Inner Circle, Connaught Place, New Delhi Connaught Place Connaught Place, New Delhi 77.2214296000 28.6323984000 Modern Indian 2200 Rs. 0 0 0 0 4 4.4 5BA829 Very Good 1942 7528 Indian Grill Room 1 Gurgaon 315, 3rd Floor, Suncity Business Tower, Golf Course Road, Gurgaon Suncity Business Tower, Golf Course Road Suncity Business Tower, Golf Course Road, Gurgaon 77.1052774000 28.4334574000 North Indian, Mughlai 1800 Rs. 1 0 1 0 3 4.5 3F7E00 Excellent 1262 18273624 Cafeteria & Co. 1 New Delhi G 14, Hudson Lane, Vijay Nagar, New Delhi Vijay Nagar Vijay Nagar, New Delhi 77.2043384000 28.6944707000 Continental, Mexican 900 Rs. 0 0 0 0 2 4.6 3F7E00 Excellent 1136 308022 Farzi Cafe 1 Gurgaon 7-8, Ground Floor, Cyber Hub, DLF Cyber City, Gurgaon Cyber Hub, DLF Cyber City Cyber Hub, DLF Cyber City, Gurgaon 77.0886879000 28.4952079000 Modern Indian 2200 Rs. 0 0 0 0 4 4.3 5BA829 Very Good 4385 18157413 Molecule Air Bar 1 Gurgaon 4th Floor, SCO 53, Main Market, Sector 29, Gurgaon Sector 29 Sector 29, Gurgaon 77.0642265000 28.4679344000 Continental, North Indian, Italian, Chinese 1500 Rs. 0 0 1 0 3 4.2 5BA829 Very Good 1809 18279449 HotMess 1 New Delhi M-11, Middle Circle, Connaught Place, New Delhi Connaught Place Connaught Place, New Delhi 77.2222380000 28.6326547000 North Indian, Mediterranean, Asian, Fast Food 1900 Rs. 1 0 1 0 3 4.3 5BA829 Very Good 1129 311057 My Bar Headquarters 1 New Delhi N-49, 2nd Floor, Connaught Place, New Delhi Connaught Place Connaught Place, New Delhi 77.2198128000 28.6307210000 North Indian, Mughlai, Chinese 1000 Rs. 0 0 0 0 3 3.7 9ACD32 Good 3010 18235

In [0]:
new_df=new_df.withColumnRenamed("res_id","restaurant Id")\
    .withColumnRenamed("name","restaurant name")\
        .withColumnRenamed("country_id","country code")
new_df.display()

restaurant Id restaurant name country code city address locality locality_verbose longitude latitude cuisines average_cost_for_two currency has_online_delivery is_delivering_now has_table_booking switch_to_order_menu price_range aggregate_rating rating_color rating_text votes 308322 Hauz Khas Social 1 New Delhi 9-A & 12, Hauz Khas Village, New Delhi Hauz Khas Village Hauz Khas Village, New Delhi 77.1944706000 28.5542851000 Continental, American, Asian, North Indian 1600 Rs. 1 0 1 0 3 4.3 5BA829 Very Good 7931 18037817 Qubitos - The Terrace Cafe 1 New Delhi C-7, Vishal Enclave, Opposite Metro Pillar 417, Rajouri Garden, New Delhi Rajouri Garden Rajouri Garden, New Delhi 77.1177015000 28.6471325000 Thai, European, Mexican, North Indian, Chinese, Cafe 1500 Rs. 0 0 1 0 3 4.5 3F7E00 Excellent 778 312345 The Hudson Cafe 1 New Delhi 2524, 1st Floor, Hudson Lane, Delhi University-GTB Nagar, New Delhi Delhi University-GTB Nagar Delhi University-GTB Nagar, New Delhi 77.2043172000 28.6949468000 Cafe, Italian, Continental, Chinese 850 Rs. 1 0 0 0 2 4.4 5BA829 Very Good 1537 307490 Summer House Cafe 1 New Delhi 1st Floor, DDA Shopping Complex, Aurobindo Place, Hauz Khas, New Delhi Hauz Khas Hauz Khas, New Delhi 77.2038090000 28.5525204000 Italian, Continental 1850 Rs. 0 0 1 0 3 4.1 5BA829 Very Good 1823 18241537 38 Barracks 1 New Delhi M-38, Outer Circle, Connaught Place, New Delhi Connaught Place Connaught Place, New Delhi 77.2228584811 28.6330248887 North Indian, Italian, Asian, American 1600 Rs. 0 0 1 0 3 4.4 5BA829 Very Good 840 18161577 Spezia Bistro 1 New Delhi 2525, 1st Floor, Hudson Lane, Delhi University-GTB Nagar, New Delhi Delhi University-GTB Nagar Delhi University-GTB Nagar, New Delhi 77.2041413000 28.6948390000 Cafe, Continental, Chinese, Italian 900 Rs. 1 0 1 0 2 4.6 3F7E00 Excellent 1071 303960 Manhattan Brewery & Bar Exchange 1 Gurgaon 1st Floor, Global Foyer Mall, Sector 43, Golf Course Road, Gurgaon Global Foyer Mall, Golf Course Road Global Foyer Mall, Golf Course Road, Gurgaon 77.0950273000 28.4602710000 Finger Food, American, Continental, North Indian, Italian 2000 Rs. 0 0 0 0 4 4.6 3F7E00 Excellent 2093 306134 The Wine Company 1 Gurgaon Cyber Hub, DLF Cyber City, Gurgaon Cyber Hub, DLF Cyber City Cyber Hub, DLF Cyber City, Gurgaon 77.0890476000 28.4962285000 Italian, European 2000 Rs. 0 0 1 0 4 2.4 FF7800 Poor 2412 18233593 Farzi Cafe 1 New Delhi 38/39, Level 1, Block E , Inner Circle, Connaught Place, New Delhi Connaught Place Connaught Place, New Delhi 77.2214296000 28.6323984000 Modern Indian 2200 Rs. 0 0 0 0 4 4.4 5BA829 Very Good 1942 7528 Indian Grill Room 1 Gurgaon 315, 3rd Floor, Suncity Business Tower, Golf Course Road, Gurgaon Suncity Business Tower, Golf Course Road Suncity Business Tower, Golf Course Road, Gurgaon 77.1052774000 28.4334574000 North Indian, Mughlai 1800 Rs. 1 0 1 0 3 4.5 3F7E00 Excellent 1262 18273624 Cafeteria & Co. 1 New Delhi G 14, Hudson Lane, Vijay Nagar, New Delhi Vijay Nagar Vijay Nagar, New Delhi 77.2043384000 28.6944707000 Continental, Mexican 900 Rs. 0 0 0 0 2 4.6 3F7E00 Excellent 1136 308022 Farzi Cafe 1 Gurgaon 7-8, Ground Floor, Cyber Hub, DLF Cyber City, Gurgaon Cyber Hub, DLF Cyber City Cyber Hub, DLF Cyber City, Gurgaon 77.0886879000 28.4952079000 Modern Indian 2200 Rs. 0 0 0 0 4 4.3 5BA829 Very Good 4385 18157413 Molecule Air Bar 1 Gurgaon 4th Floor, SCO 53, Main Market, Sector 29, Gurgaon Sector 29 Sector 29, Gurgaon 77.0642265000 28.4679344000 Continental, North Indian, Italian, Chinese 1500 Rs. 0 0 1 0 3 4.2 5BA829 Very Good 1809 18279449 HotMess 1 New Delhi M-11, Middle Circle, Connaught Place, New Delhi Connaught Place Connaught Place, New Delhi 77.2222380000 28.6326547000 North Indian, Mediterranean, Asian, Fast Food 1900 Rs. 1 0 1 0 3 4.3 5BA829 Very Good 1129 311057 My Bar Headquarters 1 New Delhi N-49, 2nd Floor, Connaught Place, New Delhi Connaught Place Connaught Place, New Delhi 77.2198128000 28.6307210000 North Indian, Mughlai, Chinese 1000 Rs. 0 0 0 0 3 3.7 9A

In [0]:
new_df.printSchema()

root
 |-- restaurant Id: long (nullable = true)
 |-- restaurant name: string (nullable = true)
 |-- country code: long (nullable = true)
 |-- city: string (nullable = true)
 |-- address: string (nullable = true)
 |-- locality: string (nullable = true)
 |-- locality_verbose: string (nullable = true)
 |-- longitude: string (nullable = true)
 |-- latitude: string (nullable = true)
 |-- cuisines: string (nullable = true)
 |-- average_cost_for_two: long (nullable = true)
 |-- currency: string (nullable = true)
 |-- has_online_delivery: long (nullable = true)
 |-- is_delivering_now: long (nullable = true)
 |-- has_table_booking: long (nullable = true)
 |-- switch_to_order_menu: long (nullable = true)
 |-- price_range: long (nullable = true)
 |-- aggregate_rating: string (nullable = true)
 |-- rating_color: string (nullable = true)
 |-- rating_text: string (nullable = true)
 |-- votes: string (nullable = true)



# 3. Data Preparation

In [0]:
new_df=new_df.withColumn("aggregate_rating",col("aggregate_rating").cast("float"))\
    .withColumn("votes",col("votes").cast("int"))\
        .withColumn("is_delivering_now",col("is_delivering_now").cast("string"))\
            .withColumn("has_online_delivery",col("has_online_delivery").cast("string"))\
                .withColumn("has_table_booking",col("has_table_booking").cast("string"))\
                    .withColumn("switch_to_order_menu",col("switch_to_order_menu").cast("string"))
new_df.display()

restaurant Id restaurant name country code city address locality locality_verbose longitude latitude cuisines average_cost_for_two currency has_online_delivery is_delivering_now has_table_booking switch_to_order_menu price_range aggregate_rating rating_color rating_text votes 308322 Hauz Khas Social 1 New Delhi 9-A & 12, Hauz Khas Village, New Delhi Hauz Khas Village Hauz Khas Village, New Delhi 77.1944706000 28.5542851000 Continental, American, Asian, North Indian 1600 Rs. 1 0 1 0 3 4.3 5BA829 Very Good 7931 18037817 Qubitos - The Terrace Cafe 1 New Delhi C-7, Vishal Enclave, Opposite Metro Pillar 417, Rajouri Garden, New Delhi Rajouri Garden Rajouri Garden, New Delhi 77.1177015000 28.6471325000 Thai, European, Mexican, North Indian, Chinese, Cafe 1500 Rs. 0 0 1 0 3 4.5 3F7E00 Excellent 778 312345 The Hudson Cafe 1 New Delhi 2524, 1st Floor, Hudson Lane, Delhi University-GTB Nagar, New Delhi Delhi University-GTB Nagar Delhi University-GTB Nagar, New Delhi 77.2043172000 28.6949468000 Cafe, Italian, Continental, Chinese 850 Rs. 1 0 0 0 2 4.4 5BA829 Very Good 1537 307490 Summer House Cafe 1 New Delhi 1st Floor, DDA Shopping Complex, Aurobindo Place, Hauz Khas, New Delhi Hauz Khas Hauz Khas, New Delhi 77.2038090000 28.5525204000 Italian, Continental 1850 Rs. 0 0 1 0 3 4.1 5BA829 Very Good 1823 18241537 38 Barracks 1 New Delhi M-38, Outer Circle, Connaught Place, New Delhi Connaught Place Connaught Place, New Delhi 77.2228584811 28.6330248887 North Indian, Italian, Asian, American 1600 Rs. 0 0 1 0 3 4.4 5BA829 Very Good 840 18161577 Spezia Bistro 1 New Delhi 2525, 1st Floor, Hudson Lane, Delhi University-GTB Nagar, New Delhi Delhi University-GTB Nagar Delhi University-GTB Nagar, New Delhi 77.2041413000 28.6948390000 Cafe, Continental, Chinese, Italian 900 Rs. 1 0 1 0 2 4.6 3F7E00 Excellent 1071 303960 Manhattan Brewery & Bar Exchange 1 Gurgaon 1st Floor, Global Foyer Mall, Sector 43, Golf Course Road, Gurgaon Global Foyer Mall, Golf Course Road Global Foyer Mall, Golf Course Road, Gurgaon 77.0950273000 28.4602710000 Finger Food, American, Continental, North Indian, Italian 2000 Rs. 0 0 0 0 4 4.6 3F7E00 Excellent 2093 306134 The Wine Company 1 Gurgaon Cyber Hub, DLF Cyber City, Gurgaon Cyber Hub, DLF Cyber City Cyber Hub, DLF Cyber City, Gurgaon 77.0890476000 28.4962285000 Italian, European 2000 Rs. 0 0 1 0 4 2.4 FF7800 Poor 2412 18233593 Farzi Cafe 1 New Delhi 38/39, Level 1, Block E , Inner Circle, Connaught Place, New Delhi Connaught Place Connaught Place, New Delhi 77.2214296000 28.6323984000 Modern Indian 2200 Rs. 0 0 0 0 4 4.4 5BA829 Very Good 1942 7528 Indian Grill Room 1 Gurgaon 315, 3rd Floor, Suncity Business Tower, Golf Course Road, Gurgaon Suncity Business Tower, Golf Course Road Suncity Business Tower, Golf Course Road, Gurgaon 77.1052774000 28.4334574000 North Indian, Mughlai 1800 Rs. 1 0 1 0 3 4.5 3F7E00 Excellent 1262 18273624 Cafeteria & Co. 1 New Delhi G 14, Hudson Lane, Vijay Nagar, New Delhi Vijay Nagar Vijay Nagar, New Delhi 77.2043384000 28.6944707000 Continental, Mexican 900 Rs. 0 0 0 0 2 4.6 3F7E00 Excellent 1136 308022 Farzi Cafe 1 Gurgaon 7-8, Ground Floor, Cyber Hub, DLF Cyber City, Gurgaon Cyber Hub, DLF Cyber City Cyber Hub, DLF Cyber City, Gurgaon 77.0886879000 28.4952079000 Modern Indian 2200 Rs. 0 0 0 0 4 4.3 5BA829 Very Good 4385 18157413 Molecule Air Bar 1 Gurgaon 4th Floor, SCO 53, Main Market, Sector 29, Gurgaon Sector 29 Sector 29, Gurgaon 77.0642265000 28.4679344000 Continental, North Indian, Italian, Chinese 1500 Rs. 0 0 1 0 3 4.2 5BA829 Very Good 1809 18279449 HotMess 1 New Delhi M-11, Middle Circle, Connaught Place, New Delhi Connaught Place Connaught Place, New Delhi 77.2222380000 28.6326547000 North Indian, Mediterranean, Asian, Fast Food 1900 Rs. 1 0 1 0 3 4.3 5BA829 Very Good 1129 311057 My Bar Headquarters 1 New Delhi N-49, 2nd Floor, Connaught Place, New Delhi Connaught Place Connaught Place, New Delhi 77.2198128000 28.6307210000 North Indian, Mughlai, Chinese 1000 Rs. 0 0 0 0 3 3.7 9A

In [0]:
new_df=new_df.withColumn("has_online_delivery",when(col("has_online_delivery")=='1','Yes')\
    .when(col("has_online_delivery")=='0','No'))\
        .withColumn("is_delivering_now",when(col("is_delivering_now")=='1','Yes')\
            .when(col('is_delivering_now')=='0','No'))\
                .withColumn("has_table_booking",when(col("has_table_booking")=='1','Yes')\
                    .when(col('has_table_booking')=='0','No'))\
                        .withColumn("switch_to_order_menu",when(col("switch_to_order_menu")=='1','Yes')\
                            .when(col('switch_to_order_menu')=='0','No'))
                

In [0]:
new_df.printSchema()

root
 |-- restaurant Id: long (nullable = true)
 |-- restaurant name: string (nullable = true)
 |-- country code: long (nullable = true)
 |-- city: string (nullable = true)
 |-- address: string (nullable = true)
 |-- locality: string (nullable = true)
 |-- locality_verbose: string (nullable = true)
 |-- longitude: string (nullable = true)
 |-- latitude: string (nullable = true)
 |-- cuisines: string (nullable = true)
 |-- average_cost_for_two: long (nullable = true)
 |-- currency: string (nullable = true)
 |-- has_online_delivery: string (nullable = true)
 |-- is_delivering_now: string (nullable = true)
 |-- has_table_booking: string (nullable = true)
 |-- switch_to_order_menu: string (nullable = true)
 |-- price_range: long (nullable = true)
 |-- aggregate_rating: float (nullable = true)
 |-- rating_color: string (nullable = true)
 |-- rating_text: string (nullable = true)
 |-- votes: integer (nullable = true)



#4. Data Transformation


Performing a broadcast join

In [0]:
new_df=new_df.join(broadcast(country_code_df),"country code","inner")

In [0]:
selected_col=["restaurant Id","restaurant name","country","city","address","currency","cuisines","price_range","average_cost_for_two","has_online_delivery","is_delivering_now","has_table_booking","switch_to_order_menu","aggregate_rating","rating_text","votes"]
data_df=new_df.select(selected_col)

In [0]:
data_df.display()

restaurant Id restaurant name country city address currency cuisines price_range average_cost_for_two has_online_delivery is_delivering_now has_table_booking switch_to_order_menu aggregate_rating rating_text votes 308322 Hauz Khas Social India New Delhi 9-A & 12, Hauz Khas Village, New Delhi Rs. Continental, American, Asian, North Indian 3 1600 Yes No Yes No 4.3 Very Good 7931 18037817 Qubitos - The Terrace Cafe India New Delhi C-7, Vishal Enclave, Opposite Metro Pillar 417, Rajouri Garden, New Delhi Rs. Thai, European, Mexican, North Indian, Chinese, Cafe 3 1500 No No Yes No 4.5 Excellent 778 312345 The Hudson Cafe India New Delhi 2524, 1st Floor, Hudson Lane, Delhi University-GTB Nagar, New Delhi Rs. Cafe, Italian, Continental, Chinese 2 850 Yes No No No 4.4 Very Good 1537 307490 Summer House Cafe India New Delhi 1st Floor, DDA Shopping Complex, Aurobindo Place, Hauz Khas, New Delhi Rs. Italian, Continental 3 1850 No No Yes No 4.1 Very Good 1823 18241537 38 Barracks India New Delhi M-38, Outer Circle, Connaught Place, New Delhi Rs. North Indian, Italian, Asian, American 3 1600 No No Yes No 4.4 Very Good 840 18161577 Spezia Bistro India New Delhi 2525, 1st Floor, Hudson Lane, Delhi University-GTB Nagar, New Delhi Rs. Cafe, Continental, Chinese, Italian 2 900 Yes No Yes No 4.6 Excellent 1071 303960 Manhattan Brewery & Bar Exchange India Gurgaon 1st Floor, Global Foyer Mall, Sector 43, Golf Course Road, Gurgaon Rs. Finger Food, American, Continental, North Indian, Italian 4 2000 No No No No 4.6 Excellent 2093 306134 The Wine Company India Gurgaon Cyber Hub, DLF Cyber City, Gurgaon Rs. Italian, European 4 2000 No No Yes No 2.4 Poor 2412 18233593 Farzi Cafe India New Delhi 38/39, Level 1, Block E , Inner Circle, Connaught Place, New Delhi Rs. Modern Indian 4 2200 No No No No 4.4 Very Good 1942 7528 Indian Grill Room India Gurgaon 315, 3rd Floor, Suncity Business Tower, Golf Course Road, Gurgaon Rs. North Indian, Mughlai 3 1800 Yes No Yes No 4.5 Excellent 1262 18273624 Cafeteria & Co. India New Delhi G 14, Hudson Lane, Vijay Nagar, New Delhi Rs. Continental, Mexican 2 900 No No No No 4.6 Excellent 1136 308022 Farzi Cafe India Gurgaon 7-8, Ground Floor, Cyber Hub, DLF Cyber City, Gurgaon Rs. Modern Indian 4 2200 No No No No 4.3 Very Good 4385 18157413 Molecule Air Bar India Gurgaon 4th Floor, SCO 53, Main Market, Sector 29, Gurgaon Rs. Continental, North Indian, Italian, Chinese 3 1500 No No Yes No 4.2 Very Good 1809 18279449 HotMess India New Delhi M-11, Middle Circle, Connaught Place, New Delhi Rs. North Indian, Mediterranean, Asian, Fast Food 3 1900 Yes No Yes No 4.3 Very Good 1129 311057 My Bar Headquarters India New Delhi N-49, 2nd Floor, Connaught Place, New Delhi Rs. North Indian, Mughlai, Chinese 3 1000 No No No No 3.7 Good 3010 18235515 FLYP@MTV India New Delhi N/57 & N/60, 1st Floor, Outer Circle, Connaught Place, New Delhi Rs. North Indian, Mexican, Italian, Continental 3 1200 No No Yes No 3.9 Good 1379 18238278 Tamasha India New Delhi 28, Kasturba Gandhi Marg, Connaught Place, New Delhi Rs. Finger Food, North Indian, Continental, Italian 3 1600 No No Yes No 3.7 Good 1801 17977777 The Barbeque Company India New Delhi HL 1-2, L Block, Jail Road, New Delhi Rs. North Indian, Chinese, Continental 3 1200 No No No No 4.2 Very Good 621 900 Saravana Bhavan India New Delhi P-13, Connaught Circus, Connaught Place, New Delhi Rs. South Indian 2 500 Yes No No No 4.3 Very Good 5172 18246991 Odeon Social India New Delhi 1st Floor, 23, Odeon Building, Radial 5, D Block, Connaught Place, New Delhi Rs. Continental, American, Asian, North Indian 3 1600 No No Yes No 4.1 Very Good 1959 18017612 Spice Kraft India Kolkata 54/1/2A, Hazra Road, Ballygunge Phari, Near Hazra Law College, Ballygunge, Kolkata Rs. Continental, Middle Eastern, Asian 3 1200 No No No No 4.8 Excellent 1424 18249144 Hoppipola India Kolkata 4th Floor, Acropolis Mall, 1858/1, Rajdanga Main Road, Kasba, Kolkata Rs. Italian, Mexican, American, Mediterranean 3 1200 Yes No No N

In [0]:
country_count=data_df.groupBy("country").agg(F.count("*").alias("records count"))
sorted_country=country_count.orderBy(F.desc("records count"))
sorted_country.display()

country records count India 720 United Kingdom 80 UAE 60 Brazil 60 South Africa 60 Turkey 40 New Zealand 40 Singapore 20 Sri Lanka 20 Phillipines 20 Qatar 20 Indonesia 20

Databricks visualization. Run in Databricks to view.

filtering top 3 countries

In [0]:
filtered_countries=sorted_country.filter((F.col("country")=='India')|(F.col("country")=='United Kingdom')|(F.col("country")=='UAE'))
filtered_countries.display()


country records count India 720 United Kingdom 80 UAE 60

Databricks visualization. Run in Databricks to view.

Observation: Zomato maximum records or transaction are from India After that United Kingdom and than from UAE

Top 5 Cities in India in which zomato is highly use

using window function

In [0]:
india_df=data_df.filter(col("country")=="India")
city_df=india_df.groupBy("city").agg(F.count("*").alias("Order count"))

window=Window.orderBy(F.desc("Order count"))
top_ranked_cities=city_df.withColumn("rank",row_number().over(window))
top_cities=top_ranked_cities.filter(F.col("rank")<=5)
top_cities.display()


city Order count rank Bangalore 20 1 Kochi 20 2 Aurangabad 20 3 Mysore 20 4 Patna 20 5

Discover the most-loved cuisines in the market

In [0]:
data_df1=data_df.withColumn("cuisines",F.split(F.col("cuisines"),", "))
cuisines_df=data_df1.withColumn("cuisines",F.explode(data_df1["cuisines"]))

In [0]:
#counting the occurence
cuisines_count=cuisines_df.groupBy("cuisines").agg(F.count("*").alias("Restaurant Count"))
top_cuisines=cuisines_count.orderBy(F.desc("Restaurant Count")).limit(10)
top_cuisines.display()

cuisines Restaurant Count North Indian 373 Chinese 270 Cafe 203 Continental 197 Italian 194 Fast Food 115 Desserts 91 American 87 Mexican 68 South Indian 68

Databricks visualization. Run in Databricks to view.

Average cost analysis by cuisine

In [0]:
data_df.printSchema()

root
 |-- restaurant Id: long (nullable = true)
 |-- restaurant name: string (nullable = true)
 |-- country: string (nullable = true)
 |-- city: string (nullable = true)
 |-- address: string (nullable = true)
 |-- currency: string (nullable = true)
 |-- cuisines: string (nullable = true)
 |-- average_cost_for_two: long (nullable = true)
 |-- has_online_delivery: string (nullable = true)
 |-- is_delivering_now: string (nullable = true)
 |-- has_table_booking: string (nullable = true)
 |-- switch_to_order_menu: string (nullable = true)
 |-- aggregate_rating: float (nullable = true)
 |-- rating_text: string (nullable = true)
 |-- votes: integer (nullable = true)



In [0]:
average_cost_df=cuisines_df.withColumn("average_cost_for_two",F.col("average_cost_for_two").cast("int"))
average_cost=average_cost_df.groupBy("cuisines").agg(F.round(avg("average_cost_for_two"),2).alias('average Cost'))
average_cost=average_cost.orderBy(F.desc("average cost")).limit(10)
average_cost.display()

cuisines average Cost Western 251673.33 Peranakan 250000.0 Indonesian 211775.0 Sunda 200000.0 Ramen 100020.0 Coffee and Tea 82525.0 Korean 40860.0 Japanese 37771.94 Sushi 37155.0 Asian 18651.33

Databricks visualization. Run in Databricks to view.

Dining Type Analysis

In [0]:
dining_count=data_df.groupBy("has_table_booking","has_online_delivery","is_delivering_now").agg(F.count("*").alias("count"))
dining_count=dining_count.orderBy(F.desc("count"))
dining_count.display()

has_table_booking has_online_delivery is_delivering_now count No No No 948 No Yes No 90 Yes No No 79 Yes Yes No 42 No Yes Yes 1

Databricks visualization. Run in Databricks to view.

Best Selling Items Analysis based on customer appeal

In [0]:
#using cusines data
cuisines_popularity=cuisines_df.groupBy("cuisines").agg(F.sum("votes").alias("total votes"))
top_cuisines=cuisines_popularity.orderBy(F.desc("total votes")).limit(10)
top_cuisines.display()

cuisines total votes North Indian 203900 Continental 120389 Italian 118634 Chinese 110711 Cafe 82045 American 68419 European 49328 Desserts 46221 Mediterranean 38107 Mexican 35870

Databricks visualization. Run in Databricks to view.

Price Range Analysis

In [0]:
price_analysis=data_df.groupBy("price_range").agg(F.round(avg("aggregate_rating"),1).alias("avg_rating"),F.sum("votes").alias("total votes"),F.count("*").alias("restaurant count"))
price_analysis.display()

price_range avg_rating total votes restaurant count 1 3.8 14061 74 3 4.0 273568 487 2 3.9 125225 337 4 4.2 100257 262

Databricks visualization. Run in Databricks to view.

#5. Advance Analysis

Competitor Analysis

In [0]:
restaurant_analysis = data_df.groupBy("restaurant name") \
  .agg(F.first("city").alias("city"),
       F.count("*").alias("listing count"),
       F.first("cuisines").alias('cuisines'),
       F.round(avg("average_cost_for_two"),2).alias("average_cost_for_two"),
       F.round(avg("aggregate_rating"),2).alias("aggregate_rating"),
       F.sum("votes").alias("votes")) \
  .orderBy(F.desc("listing count"))


In [0]:
top_restaurant=restaurant_analysis.limit(10)
top_restaurant.display()


restaurant name city listing count cuisines average_cost_for_two aggregate_rating votes Barbeque Nation Kolkata 19 North Indian, Chinese 1481.58 4.43 20418 Pizza Hut Allahabad 10 Italian, Pizza 613.0 3.89 1815 Farzi Cafe New Delhi 6 Modern Indian 1516.67 4.37 10098 Mocha Ahmedabad 6 Cafe, Continental, Desserts 925.0 4.12 2544 Chili's Pune 5 Mexican, American, Tex-Mex 1700.0 4.58 8156 The Yellow Chilli Indore 5 North Indian, Mughlai, Seafood 1060.0 3.86 997 KFC Allahabad 4 American, Fast Food 512.5 3.03 379 AB's - Absolute Barbecues Bangalore 4 European, Mediterranean, North Indian 1500.0 4.83 13400 Jamie's Italian London 4 Italian 137.5 4.05 663 Applebee's Dubai 4 American, Mexican, Burger 242.5 3.9 1057

User Behavior Analysis

In [0]:
windowspec=Window.partitionBy("city").orderBy("restaurant Id")
user_behaviour=cuisines_df.select("restaurant Id","restaurant name","city","cuisines","aggregate_rating","votes")
user_behaviour=user_behaviour.withColumn("next_rating",F.lead("aggregate_rating",1).over(windowspec))
user_behaviour=user_behaviour.withColumn("prev_rating",F.lag("aggregate_rating",1).over(windowspec))
user_behaviour=user_behaviour.withColumn("next_vote",F.lag("votes",1).over(windowspec))
user_behaviour=user_behaviour.withColumn("prev_vote",F.lag("votes",1).over(windowspec))

In [0]:
user_behaviour = user_behaviour.withColumn("rating_change", F.when(F.isnull(F.col("next_rating")), 0)
                                      .otherwise(F.round(F.col("next_rating") - F.col("aggregate_rating"),2)))
user_behaviour = user_behaviour.withColumn("votes_change", F.when(F.isnull(F.col("next_vote")), 0)
                                     .otherwise(F.round(F.col("next_vote") - F.col("votes"),2)))


In [0]:
user_behaviour.display()

restaurant Id restaurant name city cuisines aggregate_rating votes next_rating prev_rating next_vote prev_vote rating_change votes_change 5700052 Cho Gao - Crowne Plaza Abu Dhabi Abu Dhabi Thai 4.4 246 4.4 null null null 0.0 0 5700052 Cho Gao - Crowne Plaza Abu Dhabi Abu Dhabi Japanese 4.4 246 4.4 4.4 246 246 0.0 0 5700052 Cho Gao - Crowne Plaza Abu Dhabi Abu Dhabi Chinese 4.4 246 4.4 4.4 246 246 0.0 0 5700052 Cho Gao - Crowne Plaza Abu Dhabi Abu Dhabi Indonesian 4.4 246 4.4 4.4 246 246 0.0 0 5700052 Cho Gao - Crowne Plaza Abu Dhabi Abu Dhabi Vietnamese 4.4 246 3.6 4.4 246 246 -0.8 0 5700386 Sangeetha Vegetarian Restaurant Abu Dhabi Indian 3.6 268 3.6 4.4 246 246 0.0 -22 5700386 Sangeetha Vegetarian Restaurant Abu Dhabi South Indian 3.6 268 4.0 3.6 268 268 0.4 0 5701052 Applebee's Abu Dhabi American 4.0 205 4.0 3.6 268 268 0.0 63 5701052 Applebee's Abu Dhabi Mexican 4.0 205 4.0 4.0 205 205 0.0 0 5701052 Applebee's Abu Dhabi Seafood 4.0 205 4.1 4.0 205 205 0.1 0 5701446 Olive Garden Abu Dhabi Italian 4.1 422 4.1 4.0 205 205 0.0 -217 5701446 Olive Garden Abu Dhabi Pizza 4.1 422 4.0 4.1 422 422 -0.1 0 5701548 Bait El Khetyar Abu Dhabi Lebanese 4.0 380 4.0 4.1 422 422 0.0 42 5701548 Bait El Khetyar Abu Dhabi Arabian 4.0 380 4.0 4.0 380 380 0.0 0 5701548 Bait El Khetyar Abu Dhabi Middle Eastern 4.0 380 4.3 4.0 380 380 0.3 0 5701729 Sofra Istanbul Abu Dhabi Turkish 4.3 224 4.3 4.0 380 380 0.0 156 5701729 Sofra Istanbul Abu Dhabi Arabian 4.3 224 4.3 4.3 224 224 0.0 0 5701729 Sofra Istanbul Abu Dhabi Middle Eastern 4.3 224 4.2 4.3 224 224 -0.1 0 5701917 P.F. Chang's Abu Dhabi Chinese 4.2 435 4.4 4.3 224 224 0.2 -211 5701978 Pizza Di Rocco Abu Dhabi Italian 4.4 471 4.4 4.2 435 435 0.0 -36 5701978 Pizza Di Rocco Abu Dhabi Pizza 4.4 471 4.0 4.4 471 471 -0.4 0 5702418 Gazebo Abu Dhabi Indian 4.0 355 4.0 4.4 471 471 0.0 116 5702418 Gazebo Abu Dhabi North Indian 4.0 355 4.0 4.0 355 355 0.0 0 5702418 Gazebo Abu Dhabi Mughlai 4.0 355 4.0 4.0 355 355 0.0 0 5702418 Gazebo Abu Dhabi Biryani 4.0 355 4.6 4.0 355 355 0.6 0 5702574 The Cheesecake Factory Abu Dhabi American 4.6 586 4.6 4.0 355 355 0.0 -231 5702574 The Cheesecake Factory Abu Dhabi Desserts 4.6 586 4.0 4.6 586 586 -0.6 0 5702615 Via Delhi Abu Dhabi Indian 4.0 525 4.0 4.6 586 586 0.0 61 5702615 Via Delhi Abu Dhabi North Indian 4.0 525 4.0 4.0 525 525 0.0 0 5702615 Via Delhi Abu Dhabi Chinese 4.0 525 4.9 4.0 525 525 0.9 0 5703500 Punjab Grill Abu Dhabi Indian 4.9 216 4.9 4.0 525 525 0.0 309 5703500 Punjab Grill Abu Dhabi North Indian 4.9 216 4.0 4.9 216 216 -0.9 0 5704118 Tikka Tonight Abu Dhabi Pakistani 4.0 277 4.0 4.9 216 216 0.0 -61 5704118 Tikka Tonight Abu Dhabi Afghani 4.0 277 4.0 4.0 277 277 0.0 0 5704118 Tikka Tonight Abu Dhabi Indian 4.0 277 4.0 4.0 277 277 0.0 0 5704118 Tikka Tonight Abu Dhabi Hyderabadi 4.0 277 4.2 4.0 277 277 0.2 0 5704168 Salt Abu Dhabi Fast Food 4.2 228 4.2 4.0 277 277 0.0 49 5704168 Salt Abu Dhabi Burger 4.2 228 4.5 4.2 228 228 0.3 0 5704202 Hot Palayok Abu Dhabi Filipino 4.5 162 4.5 4.2 228 228 0.0 66 5704202 Hot Palayok Abu Dhabi Japanese 4.5 162 4.5 4.5 162 162 0.0 0 5704202 Hot Palayok Abu Dhabi Asian 4.5 162 4.6 4.5 162 162 0.1 0 5704255 Famous Dave's Barbecue Abu Dhabi American 4.6 376 4.6 4.5 162 162 0.0 -214 18212135 Denny's Abu Dhabi American 4.6 207 4.3 4.6 376 376 -0.3 169 18235425 Indian By Nature Abu Dhabi Indian 4.3 180 4.7 4.6 207 207 0.4 27 18253896 Tamba Abu Dhabi Indian 4.7 201 4.6 4.3 180 180 -0.1 -21 18277098 Genghis Grill Abu Dhabi Asian 4.6 81 null 4.7 201 201 0.0 120 3400005 Time2Eat - Mama Chicken Agra North Indian 3.6 94 3.7 null null null 0.1 0 3400016 Pind Balluchi Agra North Indian 3.7 175 3.7 3.6 94 94 0.0 -81 3400016 Pind Balluchi Agra Mughlai 3.7 175 4.2 3.7 175 175 0.5 0 3400017 Pinch Of Spice Agra North Indian 4.2 177 4.2 3.7 175 175 0.0 -2 3400017 Pinch Of Spice Agra Chinese 4.2 177 4.2 4.2 177 177 0.0 0 3400017 Pinch Of Spice Agra Mughlai 4.2 177 4.1 4.2 177 177 -0.1 0 3400019 Dasaprakash Restaurant Agra South Indian 4.1